# GeoSpatial Data Project

Your result will be a city and a neighbourhood/zip code or adress/coordinates.

In [1]:
import requests
import json
import pandas as pd
from getpass import getpass
import os
from dotenv import load_dotenv
import geopandas as gpd
from cartoframes.viz import Map, Layer, popup_element
import time
import folium
from folium import Choropleth, Circle, Marker, Icon, Map
from folium.plugins import HeatMap, MarkerCluster
from pymongo import MongoClient
!pip install geopy
from geopy.geocoders import Nominatim

In [2]:
client = MongoClient("localhost:27017")

In [3]:
db = client["Ironhack"]
c = db.get_collection("companies")

### 1. I want to check in which cities there are tech startups that have raised at least 1 million dollars. 

In [4]:
cond1 = {"category_code": "design"}
cond2 = {"category_code": "games_video"}
cond3 = {"category_code": "web"}
cond4 = {"category_code": "software"}

cond5 = {"tag_list":{"$regex":"startup"}}
cond6 = {"total_money_raised":{"$regex":'M'}}


filters = {
    '$or': [cond1, cond2, cond3, cond4],
    '$and': [cond5, cond6],
}

projection = {'name': 1, '_id': 0, 'offices.city': 1, 'offices.state_code': 1, 'number_of_employees': 1, 'category_code': 1}

cities = list(c.find(filters, projection).sort('number_of_employees', -1))
cities

[{'name': 'Kareo',
  'category_code': 'software',
  'number_of_employees': 250,
  'offices': [{'city': 'Irvine', 'state_code': 'CA'}]}]

In [5]:
cond5 = {"tag_list":{"$regex":"startup"}}
cond6 = {"total_money_raised":{"$regex":'M'}}


filters = {
    '$and': [cond5, cond6],
}

projection = {'name': 1, '_id': 0, 'offices.city': 1, 'offices.country_code': 1, 'number_of_employees': 1, 'category_code': 1, 'total_money_raised': 1, 'tag_list': 1}

cities_2 = list(c.find(filters, projection).sort('number_of_employees', -1))
cities_2

[{'name': 'Kareo',
  'category_code': 'software',
  'number_of_employees': 250,
  'tag_list': 'vc-firm, startup, cloud-based-solutions, health-management',
  'total_money_raised': '$51.4M',
  'offices': [{'city': 'Irvine', 'country_code': 'USA'}]},
 {'name': 'SecondMarket',
  'category_code': 'finance',
  'number_of_employees': 140,
  'tag_list': 'private-company-stock, auction-rate-securities, investor-communications, startup, new-york-tech, bitcoin',
  'total_money_raised': '$34.2M',
  'offices': [{'city': 'New York', 'country_code': 'USA'},
   {'city': 'San Francsico', 'country_code': 'USA'}]},
 {'name': 'Echo',
  'category_code': 'enterprise',
  'number_of_employees': 50,
  'tag_list': 'platform, real-time, website, digital, social-media, ratings, comment, blog, poll, polls, comments, rate, javascript, widget, database, publishing, media, startups',
  'total_money_raised': '$4.8M',
  'offices': [{'city': 'San francisco', 'country_code': 'USA'}]},
 {'name': 'Startup Weekend',
  'cat

The cities that meet these conditions are: Irvine, New York, San Francisco, Seattle, London and Minneapolis. But these aren't the best cities to live with children.

### 2. I'll check in which cities there are more video games companies (so that my designers can share talks and knowledge with other video games designers).

In [6]:
filters = {"category_code": "games_video"}

projection = {'name': 1, '_id': 0, 'offices.city': 1, 'offices.country_code': 1, 'number_of_employees': 1, 'category_code': 1, 'total_money_raised': 1}

cities_3 = list(c.find(filters, projection))
cities_3

[{'name': 'Flektor',
  'category_code': 'games_video',
  'number_of_employees': None,
  'total_money_raised': '$0',
  'offices': [{'city': 'Culver City', 'country_code': 'USA'}]},
 {'name': 'Lala',
  'category_code': 'games_video',
  'number_of_employees': None,
  'total_money_raised': '$44.2M',
  'offices': [{'city': 'Palo Alto', 'country_code': 'USA'}]},
 {'name': 'Joost',
  'category_code': 'games_video',
  'number_of_employees': 0,
  'total_money_raised': '$45M',
  'offices': [{'city': 'New York', 'country_code': 'USA'}]},
 {'name': 'Babelgum',
  'category_code': 'games_video',
  'number_of_employees': None,
  'total_money_raised': '$13.2M',
  'offices': [{'city': 'London', 'country_code': 'GBR'}]},
 {'name': 'Sparter',
  'category_code': 'games_video',
  'number_of_employees': None,
  'total_money_raised': '$0',
  'offices': [{'city': None, 'country_code': 'USA'}]},
 {'name': 'Kyte',
  'category_code': 'games_video',
  'number_of_employees': 40,
  'total_money_raised': '$23.4M',
 

In [7]:
videogames_cities = set()

for entry in cities_3:
    offices = entry.get('offices', [])
    for office in offices:
        city = office.get('city', '')
        if city:
            videogames_cities.add(city)
print(sorted(list(videogames_cities)))

['2nd Floor', '46395 Bocholt', 'Aachen', 'Abercynon', 'Acton', 'Agoura Hills', 'Alexandria', 'Aliso Viejo', 'Alpharetta', 'Amarillo', 'Amersham', 'Amsterdam', 'Andover', 'Ann Arbor', 'Astoria', 'Athens', 'Atherton', 'Atlanta', 'Auckland', 'Austin', 'Baltimore', 'Bangalore', 'Barcelona', 'Bay Area', 'Bear', 'Beijing', 'Beirut', 'Belfast', 'Bellevue', 'Belmont', 'Berkeley', 'Berkshire', 'Berlin', 'Bethesda', 'Beverly Hills', 'Bilthoven', 'Birmingham', 'Boca Raton', 'BodÃ¸', 'Bogota', 'Bologna', 'Boothwyn', 'Boston', 'Bothell', 'Boulder', 'Bournemouth', 'Branford', 'Brea', 'Bretten', 'Brooklyn', 'Broughty Ferry, Dundee', 'Bucharest', 'Bucuresti', 'Budapest', 'Buenos Aires', 'Burbank', 'Burlingame', 'CALUIRE ET CUIRE', 'CH-8050 ZÃ¼rich', 'Calabasas', 'Caldwell', 'Calgary', 'Calgary, Alberta', 'California', 'Cambridge', 'Campbell', 'Carlsbad', 'Castleford', 'Celje', 'Century City', 'Cesena', 'Champaign', 'Chicago', 'Chirens', 'Ciudad de Buenos Aires', 'Clearwater', 'Collingswood', 'Cologne'

In [8]:
# I create a dictionary to store city counts
city_counts = {}

for entry in cities_3:
    offices = entry.get('offices', [])
    for office in offices:
        city = office.get('city', '')
        if city:
            city_counts[city] = city_counts.get(city, 0) + 1

for city, count in city_counts.items():
    print(f'{city}: {count}')

Culver City: 4
Palo Alto: 16
New York: 75
London: 36
San Francisco: 68
San Diego: 5
San Bruno: 1
Los Angeles: 31
Ramat Gan: 6
Budapest: 1
NYC: 1
Moscow: 3
San Mateo: 9
46395 Bocholt: 1
Burlingame: 4
Redwood City: 6
Seattle: 13
Huntsville: 1
Mountain View: 6
Burbank: 3
Waltham: 1
San Antonio: 2
Newburyport: 1
Las Vegas: 3
Pittsburgh: 3
Bellevue: 5
Belmont: 1
Santa Monica: 14
Fort Lauderdale: 1
Andover: 2
Corte Madera: 1
Boston: 5
Toronto: 6
San Jose: 6
Newton: 1
Austin: 8
Eden Prairie: 1
West Palm Beach: 2
Singapore: 1
Berkeley: 4
Solana Beach: 2
Sunnyvale: 8
Tel Aviv: 4
Santa Clara: 3
Poughkeepsie: 1
Norderstedt: 1
Wimbledon: 1
Ann Arbor: 1
CH-8050 ZÃ¼rich: 1
Silver Spring: 1
Campbell: 1
Tenafly: 1
Los Angleles: 1
Sherman Oaks: 2
Rockville: 1
Sausalito: 1
King of Prussia: 1
Paris: 17
Redmond: 2
Edison: 1
Philadelphia: 5
Baltimore: 2
Kolkata: 2
Amsterdam: 6
Limerick: 1
Boulder: 3
Stockholm''': 1
Grand Rapids: 1
Doha: 1
Cambridge: 8
Berlin: 8
Mellieha: 2
Santa Cruz: 1
Tulsa: 1
Hollywood:

In [9]:
# Sort the keys alphabetically
sorted_keys = sorted(city_counts.keys())

# Print the sorted keys
for key in sorted_keys:
    print(f'{key}: {city_counts[key]}')


2nd Floor: 1
46395 Bocholt: 1
Aachen: 1
Abercynon: 1
Acton: 1
Agoura Hills: 1
Alexandria: 1
Aliso Viejo: 1
Alpharetta: 1
Amarillo: 2
Amersham: 1
Amsterdam: 6
Andover: 2
Ann Arbor: 1
Astoria: 1
Athens: 1
Atherton: 1
Atlanta: 3
Auckland: 1
Austin: 8
Baltimore: 2
Bangalore: 2
Barcelona: 3
Bay Area: 1
Bear: 1
Beijing: 5
Beirut: 1
Belfast: 1
Bellevue: 5
Belmont: 1
Berkeley: 4
Berkshire: 1
Berlin: 8
Bethesda: 1
Beverly Hills: 6
Bilthoven: 1
Birmingham: 1
Boca Raton: 2
BodÃ¸: 1
Bogota: 1
Bologna: 1
Boothwyn: 1
Boston: 5
Bothell: 1
Boulder: 3
Bournemouth: 1
Branford: 1
Brea: 1
Bretten: 1
Brooklyn: 6
Broughty Ferry, Dundee: 1
Bucharest: 1
Bucuresti: 1
Budapest: 1
Buenos Aires: 3
Burbank: 3
Burlingame: 4
CALUIRE ET CUIRE: 1
CH-8050 ZÃ¼rich: 1
Calabasas: 1
Caldwell: 1
Calgary: 1
Calgary, Alberta: 2
California: 1
Cambridge: 8
Campbell: 1
Carlsbad: 2
Castleford: 1
Celje: 1
Century City: 1
Cesena: 1
Champaign: 1
Chicago: 8
Chirens: 1
Ciudad de Buenos Aires: 1
Clearwater: 1
Collingswood: 1
Cologne: 3

### 3. The chosen city:

I have picked **Tokyo** because among the 10 best cities in the world to live with children (as reported by an article in 2021) this is the one with more video games companies:

https://immigrantinvest.com/insider/best-cities-to-raise-a-family-2021-en/ 


In [10]:
filters = {"category_code": "games_video", "offices.city": "Tokyo"
    
    
}

projection = {'name': 1, '_id': 0, 'offices': 1, 'category_code': 1}

Tok = list(c.find(filters, projection).sort('number_of_employees', -1))
Tok

[{'name': 'DeNA',
  'category_code': 'games_video',
  'offices': [{'description': 'Headquarters',
    'address1': 'Shibuya Hikarie, 2-21-1',
    'address2': 'Shibuya, Shibuya-ku',
    'zip_code': '150-8510',
    'city': 'Tokyo',
    'state_code': None,
    'country_code': 'JPN',
    'latitude': None,
    'longitude': None}]},
 {'name': 'DeNA',
  'category_code': 'games_video',
  'offices': [{'description': 'Headquarters',
    'address1': 'Shibuya Hikarie, 2-21-1',
    'address2': 'Shibuya, Shibuya-ku',
    'zip_code': '150-8510',
    'city': 'Tokyo',
    'state_code': None,
    'country_code': 'JPN',
    'latitude': None,
    'longitude': None}]},
 {'name': 'GREE',
  'category_code': 'games_video',
  'offices': [{'description': 'Headquarters',
    'address1': 'Roppongi-Hills Mori Tower, 6-10-1, Roppongi',
    'address2': 'Minato-ku',
    'zip_code': '106-0032',
    'city': 'Tokyo',
    'state_code': None,
    'country_code': 'JPN',
    'latitude': None,
    'longitude': None}]},
 {'nam

In [11]:
# Extract the relevant information from the nested structure
tok_df = []
for entry in Tok:
    name = entry['name']
    category_code = entry['category_code']
    for office in entry['offices']:
        description = office.get('description', '')
        address1 = office.get('address1', '')
        address2 = office.get('address2', '')
        zip_code = office.get('zip_code', '')
        city = office.get('city', '')
        country_code = office.get('country_code', '')
        tok_df.append([name, category_code, description, address1, address2, zip_code, city, country_code])

# Create the DataFrame
columns = ['name', 'category_code', 'description', 'address1', 'address2', 'zip_code', 'city', 'country_code']
tok_df = pd.DataFrame(tok_df, columns=columns)
tok_df

name category_code    description  \
0       DeNA   games_video   Headquarters   
1       DeNA   games_video   Headquarters   
2       GREE   games_video   Headquarters   
3     Utagoe   games_video    Headquarter   
4     Utagoe   games_video  Branch Office   
5     Utagoe   games_video    Headquarter   
6     Utagoe   games_video  Branch Office   
7    Niwango   games_video           None   
8    Natasha   games_video    Headquarter   
9   DigiDock   games_video    Headquarter   
10  Metacast   games_video    Headquarter   

                                        address1  \
0                        Shibuya Hikarie, 2-21-1   
1                        Shibuya Hikarie, 2-21-1   
2    Roppongi-Hills Mori Tower, 6-10-1, Roppongi   
3                         5-10-1 #1001, Shinjuku   
4                 111 N Market Street, 6th Floor   
5                         5-10-1 #1001, Shinjuku   
6                 111 N Market Street, 6th Floor   
7                           Hamacho Center Bldg.   
8                       Shimokitazawa 2-28-7, 2F   
9                          6-10-202 Sumiyosichou   
10  NGA Minami Aoyama Bldg. XII 4F, Aoyama 7-3-1   

                               address2  zip_code      city country_code  
0                   Shibuya, Shibuya-ku  150-8510     Tokyo          JPN  
1                   Shibuya, Shibuya-ku  150-8510     Tokyo          JPN  
2                             Minato-ku  106-0032     Tokyo          JPN  
3                           Shinjuku-ku  160-0022     Tokyo          JPN  
4                                           95113  San Jose          USA  
5                           Shinjuku-ku  160-0022     Tokyo          JPN  
6                                           95113  San Jose          USA  
7   2-31-1 Nihonbashi-Hama-cho, Chuo-ku   103-007     Tokyo          JPN  
8                           Setagaya-ku  155-0031     Tokyo          JPN  
9                           Shinjuku-ku  162-0065     Tokyo          JPN  
10                            Minato-ku  107-0062     Tokyo          JPN

In [12]:
# Checking for duplicated data

print(f"Dataset has {tok_df.duplicated().sum()} duplicated data.")

Dataset has 3 duplicated data.


In [13]:
# Dropping the duplicates

tok_df = tok_df.drop_duplicates() 

# Checking if the previous step has worked:

print(f"Dataset has {tok_df.duplicated().sum()} duplicated data.")
tok_df

Dataset has 0 duplicated data.


name category_code    description  \
0       DeNA   games_video   Headquarters   
2       GREE   games_video   Headquarters   
3     Utagoe   games_video    Headquarter   
4     Utagoe   games_video  Branch Office   
7    Niwango   games_video           None   
8    Natasha   games_video    Headquarter   
9   DigiDock   games_video    Headquarter   
10  Metacast   games_video    Headquarter   

                                        address1  \
0                        Shibuya Hikarie, 2-21-1   
2    Roppongi-Hills Mori Tower, 6-10-1, Roppongi   
3                         5-10-1 #1001, Shinjuku   
4                 111 N Market Street, 6th Floor   
7                           Hamacho Center Bldg.   
8                       Shimokitazawa 2-28-7, 2F   
9                          6-10-202 Sumiyosichou   
10  NGA Minami Aoyama Bldg. XII 4F, Aoyama 7-3-1   

                               address2  zip_code      city country_code  
0                   Shibuya, Shibuya-ku  150-8510     Tokyo          JPN  
2                             Minato-ku  106-0032     Tokyo          JPN  
3                           Shinjuku-ku  160-0022     Tokyo          JPN  
4                                           95113  San Jose          USA  
7   2-31-1 Nihonbashi-Hama-cho, Chuo-ku   103-007     Tokyo          JPN  
8                           Setagaya-ku  155-0031     Tokyo          JPN  
9                           Shinjuku-ku  162-0065     Tokyo          JPN  
10                            Minato-ku  107-0062     Tokyo          JPN

In [14]:
tok_df['lat'] = None  
tok_df['lon'] = None  
tok_df

/var/folders/_b/4s7pp99j1qq9lxsqpjphc78m0000gn/T/ipykernel_83833/1429768547.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tok_df['lat'] = None
/var/folders/_b/4s7pp99j1qq9lxsqpjphc78m0000gn/T/ipykernel_83833/1429768547.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tok_df['lon'] = None


name category_code    description  \
0       DeNA   games_video   Headquarters   
2       GREE   games_video   Headquarters   
3     Utagoe   games_video    Headquarter   
4     Utagoe   games_video  Branch Office   
7    Niwango   games_video           None   
8    Natasha   games_video    Headquarter   
9   DigiDock   games_video    Headquarter   
10  Metacast   games_video    Headquarter   

                                        address1  \
0                        Shibuya Hikarie, 2-21-1   
2    Roppongi-Hills Mori Tower, 6-10-1, Roppongi   
3                         5-10-1 #1001, Shinjuku   
4                 111 N Market Street, 6th Floor   
7                           Hamacho Center Bldg.   
8                       Shimokitazawa 2-28-7, 2F   
9                          6-10-202 Sumiyosichou   
10  NGA Minami Aoyama Bldg. XII 4F, Aoyama 7-3-1   

                               address2  zip_code      city country_code  \
0                   Shibuya, Shibuya-ku  150-8510     Tokyo          JPN   
2                             Minato-ku  106-0032     Tokyo          JPN   
3                           Shinjuku-ku  160-0022     Tokyo          JPN   
4                                           95113  San Jose          USA   
7   2-31-1 Nihonbashi-Hama-cho, Chuo-ku   103-007     Tokyo          JPN   
8                           Setagaya-ku  155-0031     Tokyo          JPN   
9                           Shinjuku-ku  162-0065     Tokyo          JPN   
10                            Minato-ku  107-0062     Tokyo          JPN   

     lat   lon  
0   None  None  
2   None  None  
3   None  None  
4   None  None  
7   None  None  
8   None  None  
9   None  None  
10  None  None

In [15]:
desired_value = 'Tokyo'
tok_df = tok_df[tok_df['city'] == desired_value]
tok_df

name category_code   description  \
0       DeNA   games_video  Headquarters   
2       GREE   games_video  Headquarters   
3     Utagoe   games_video   Headquarter   
7    Niwango   games_video          None   
8    Natasha   games_video   Headquarter   
9   DigiDock   games_video   Headquarter   
10  Metacast   games_video   Headquarter   

                                        address1  \
0                        Shibuya Hikarie, 2-21-1   
2    Roppongi-Hills Mori Tower, 6-10-1, Roppongi   
3                         5-10-1 #1001, Shinjuku   
7                           Hamacho Center Bldg.   
8                       Shimokitazawa 2-28-7, 2F   
9                          6-10-202 Sumiyosichou   
10  NGA Minami Aoyama Bldg. XII 4F, Aoyama 7-3-1   

                               address2  zip_code   city country_code   lat  \
0                   Shibuya, Shibuya-ku  150-8510  Tokyo          JPN  None   
2                             Minato-ku  106-0032  Tokyo          JPN  None   
3                           Shinjuku-ku  160-0022  Tokyo          JPN  None   
7   2-31-1 Nihonbashi-Hama-cho, Chuo-ku   103-007  Tokyo          JPN  None   
8                           Setagaya-ku  155-0031  Tokyo          JPN  None   
9                           Shinjuku-ku  162-0065  Tokyo          JPN  None   
10                            Minato-ku  107-0062  Tokyo          JPN  None   

     lon  
0   None  
2   None  
3   None  
7   None  
8   None  
9   None  
10  None

In [16]:
tok_df.at[0, 'lat'] = 35.6948056
tok_df.at[0, 'lon'] = 139.6393433
tok_df.at[2, 'lat'] = 35.6587603
tok_df.at[2, 'lon'] = 139.72941112
tok_df.at[3, 'lat'] = 35.7122007
tok_df.at[3, 'lon'] = 139.7021159
tok_df.at[7, 'lat'] = 35.6871672
tok_df.at[7, 'lon'] = 139.7867856
tok_df.at[8, 'lat'] = 35.6633886
tok_df.at[8, 'lon'] = 139.6655874
tok_df.at[9, 'lat'] = 35.6898602
tok_df.at[9, 'lon'] = 139.6899144
tok_df.at[10, 'lat'] = 35.664797
tok_df.at[10, 'lon'] = 139.7086912

tok_df

name category_code   description  \
0       DeNA   games_video  Headquarters   
2       GREE   games_video  Headquarters   
3     Utagoe   games_video   Headquarter   
7    Niwango   games_video          None   
8    Natasha   games_video   Headquarter   
9   DigiDock   games_video   Headquarter   
10  Metacast   games_video   Headquarter   

                                        address1  \
0                        Shibuya Hikarie, 2-21-1   
2    Roppongi-Hills Mori Tower, 6-10-1, Roppongi   
3                         5-10-1 #1001, Shinjuku   
7                           Hamacho Center Bldg.   
8                       Shimokitazawa 2-28-7, 2F   
9                          6-10-202 Sumiyosichou   
10  NGA Minami Aoyama Bldg. XII 4F, Aoyama 7-3-1   

                               address2  zip_code   city country_code  \
0                   Shibuya, Shibuya-ku  150-8510  Tokyo          JPN   
2                             Minato-ku  106-0032  Tokyo          JPN   
3                           Shinjuku-ku  160-0022  Tokyo          JPN   
7   2-31-1 Nihonbashi-Hama-cho, Chuo-ku   103-007  Tokyo          JPN   
8                           Setagaya-ku  155-0031  Tokyo          JPN   
9                           Shinjuku-ku  162-0065  Tokyo          JPN   
10                            Minato-ku  107-0062  Tokyo          JPN   

          lat         lon  
0   35.694806  139.639343  
2    35.65876  139.729411  
3   35.712201  139.702116  
7   35.687167  139.786786  
8   35.663389  139.665587  
9    35.68986  139.689914  
10  35.664797  139.708691

#### COMPANY SCHEME:

- 20 Designers
- 5 UI/UX Engineers
- 10 Frontend Developers
- 15 Data Engineers
- 5 Backend Developers
- 20 Account Managers
- 1 Maintenance guy that loves basketball
- 10 Executives
- 1 CEO/President

#### CONDITIONS:

- Designers like to go to design talks and share knowledge. There must be some nearby companies that also do design.
- 30% of the company staff have at least 1 child.
- Developers like to be near successful tech startups that have raised at least 1 Million dollars.
- Executives like Starbucks A LOT. Ensure there's a starbucks not too far.
- Account managers need to travel a lot.
- Everyone in the company is between 25 and 40, give them some place to go party.
- The CEO is vegan.
- If you want to make the maintenance guy happy, a basketball stadium must be around 10 Km.
- The office dog—"Dobby" needs a hairdresser every month. Ensure there's one not too far away.

### 4. Tokyo's map with Starbucks.

In [17]:
load_dotenv()
token = os.getenv("token")

In [18]:
# Tokyo's coordinates

lat = 35.652832
lon = 139.839478

In [19]:
def foursquare_places(venue, token, latitude=35.652832, longitude=139.839478, limit=50):
    endpoint = f'https://api.foursquare.com/v3/places/search?query={venue}'

    if latitude is not None and longitude is not None:
        endpoint += f'&ll={latitude},{longitude}'

    endpoint += f'&limit={limit}'  # Add the limit parameter

    headers = {
        "accept": "application/json",
        "Authorization": token
    }

    try:
        response = requests.get(endpoint, headers=headers)
        response.raise_for_status()
        data = response.json()
        venues = data.get('results', [])
        results = []
        for venue in venues:
            name = venue.get('name')
            location = venue.get('geocodes', {}).get('main', {})
            lat = location.get('latitude')
            lng = location.get('longitude')
            results.append({
                'name': name,
                'lat': lat,
                'lng': lng
            })
        return results
    except requests.exceptions.RequestException as e:
        print(f"Error: {e}")
        return []
    finally:
        time.sleep(3)  

In [20]:
venue = "starbucks"
starbucks = foursquare_places(venue, token, latitude=35.652832, longitude=139.839478, limit=50)
starbucks

[{'name': 'Starbucks', 'lat': 35.628851, 'lng': 139.656619},
 {'name': 'Starbucks (スターバックス)', 'lat': 35.641843, 'lng': 139.803035},
 {'name': 'Starbucks (スターバックス)', 'lat': 35.682924, 'lng': 139.825661},
 {'name': 'Starbucks (スターバックス)', 'lat': 35.666117, 'lng': 139.80424},
 {'name': 'Starbucks', 'lat': 35.630064, 'lng': 139.793814},
 {'name': 'Starbucks (スターバックス)', 'lat': 35.656502, 'lng': 139.782201},
 {'name': 'Starbucks', 'lat': 35.697643, 'lng': 139.826055},
 {'name': 'Starbucks (スターバックス)', 'lat': 35.62791, 'lng': 139.7735},
 {'name': 'Starbucks (スターバックス)', 'lat': 35.709936, 'lng': 139.810832},
 {'name': 'Starbucks', 'lat': 35.679391, 'lng': 139.780739},
 {'name': 'Starbucks (スターバックス)', 'lat': 35.655896, 'lng': 139.796233},
 {'name': 'Starbucks (スターバックス)', 'lat': 35.696362, 'lng': 139.815762},
 {'name': 'Starbucks', 'lat': 35.655073, 'lng': 139.792758},
 {'name': 'Starbucks', 'lat': 35.686911, 'lng': 139.781496},
 {'name': 'Starbucks (スターバックス)', 'lat': 35.679778, 'lng': 139.76483},


In [21]:
starbucks_d = pd.DataFrame(starbucks)

starbucks_d.to_csv("starbucks.csv", index=False)

# Specify the folder path and filename for the CSV file
folder_path = "/Users/usuari/Desktop/Ironhack/BOOTCAMP/projects/project-3/data"
file_name = "starbucks.csv"

# Combine the folder path and filename to create the full file path
full_file_path = f"{folder_path}/{file_name}"

# Export the DataFrame to the specified folder
starbucks_d.to_csv(full_file_path, index=False)

In [22]:
# Create a base map centered around Tokyo, Japan
m = Map(location=[35.652832, 139.839478], zoom_start=13)

# Add Starbucks locations to the map
for location in starbucks:
    tooltip = location['name']
    icon = folium.Icon(color='green', icon_color='white', icon='coffee', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Display the m
m

### 5. Tokyo's map with the video games companies

In [23]:
# Create a base map centered around Tokyo, Japan
m = Map(location=[35.652832, 139.839478], zoom_start=13)

# Add Starbucks locations to the map
for location in starbucks:
    tooltip = location['name']
    icon = folium.Icon(color='green', icon_color='white', icon='coffee', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)


for index, row in tok_df.iterrows():
    tooltip = row['name']  # Move the tooltip line inside the loop
    icon = folium.Icon(color='red', icon_color='black', icon='gamepad', prefix='fa')
    folium.Marker(
        location=[row['lat'], row['lon']],
        tooltip=tooltip,  # Set the tooltip for the marker
        icon=icon  # Set the custom icon for the marker
    ).add_to(m)

# Display the map
m

### 6. Tokyo's map with dog grooming places

In [24]:
venue = "pet grooming"
dog = foursquare_places(venue, token, latitude=35.652832, longitude=139.839478, limit=50)
dog

[{'name': "Peter Pan's Flight (ピーターパン空の旅)",
  'lat': 35.631696,
  'lng': 139.881664},
 {'name': 'petit madoca (マツモトキヨシドラッグストア南葛西店)',
  'lat': 35.646662,
  'lng': 139.872074},
 {'name': 'PET SOUNDS RECORD', 'lat': 35.619839, 'lng': 139.703477},
 {'name': 'Pet Plus', 'lat': 35.627844, 'lng': 139.773223},
 {'name': 'Petit Rire', 'lat': 35.65947, 'lng': 139.87661},
 {'name': 'HAIR & GROOMING YOSHIZAWA Inc. PREMIUM',
  'lat': 35.666333,
  'lng': 139.778811},
 {'name': 'PET FOREST Saginuma (ペットフォレスト 鷺沼店)',
  'lat': 35.57502,
  'lng': 139.576507},
 {'name': 'PET HOUSE HARA', 'lat': 35.65634, 'lng': 139.734513},
 {'name': 'PET-SPA 高輪店', 'lat': 35.629294, 'lng': 139.733782},
 {'name': "Men's Grooming Salon & Store by kakimoto arms",
  'lat': 35.660676,
  'lng': 139.728928},
 {'name': 'PET‐SPA白金プラチナ通り店', 'lat': 35.638281, 'lng': 139.722963},
 {'name': 'All Pet クリニック', 'lat': 35.663254, 'lng': 139.720322},
 {'name': 'e・bis・pet (エビスペット)', 'lat': 35.647674, 'lng': 139.717503},
 {'name': "Men's Groo

In [25]:
dog_d = pd.DataFrame(dog)

In [26]:
dog_d.to_csv("dog.csv", index=False)

# Specify the folder path and filename for the CSV file
folder_path = "/Users/usuari/Desktop/Ironhack/BOOTCAMP/projects/project-3/data"
file_name = "dog.csv"

# Combine the folder path and filename to create the full file path
full_file_path = f"{folder_path}/{file_name}"

# Export the DataFrame to the specified folder
dog_d.to_csv(full_file_path, index=False)

In [27]:
# Create a base map centered around Tokyo, Japan
m = Map(location=[35.652832, 139.839478], zoom_start=13)

# Add Starbucks locations to the map
for location in starbucks:
    tooltip = location['name']
    icon = folium.Icon(color='green', icon_color='white', icon='coffee', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)


for index, row in tok_df.iterrows():
    tooltip = row['name']  # Move the tooltip line inside the loop
    icon = folium.Icon(color='red', icon_color='black', icon='gamepad', prefix='fa')
    folium.Marker(
        location=[row['lat'], row['lon']],
        tooltip=tooltip,  # Set the tooltip for the marker
        icon=icon  # Set the custom icon for the marker
    ).add_to(m)

for location in dog:
    tooltip = location['name']
    icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Display the map
m

### 7. Tokyo's map with metro stations

In [28]:
venue = "metro"
train = foursquare_places(venue, token, latitude=35.652832, longitude=139.839478, limit=50)
train

[{'name': 'Higashi-ojima Station (S16) (東大島駅)',
  'lat': 35.689813,
  'lng': 139.847545},
 {'name': 'Tokyo Station (東京駅)', 'lat': 35.681324, 'lng': 139.76685},
 {'name': 'Akihabara Station (秋葉原駅)', 'lat': 35.69867, 'lng': 139.772096},
 {'name': 'Tatsumi Station (Y23) (辰巳駅)', 'lat': 35.645805, 'lng': 139.810277},
 {'name': 'Kasai Station (T17) (葛西駅)', 'lat': 35.663611, 'lng': 139.872666},
 {'name': 'Shinjuku Station (新宿駅)', 'lat': 35.689608, 'lng': 139.70056},
 {'name': 'Yurakucho Line Toyosu Station (Y22) (有楽町線 豊洲駅)',
  'lat': 35.655,
  'lng': 139.79611},
 {'name': 'Funabori Station (S17) (船堀駅)', 'lat': 35.683777, 'lng': 139.863805},
 {'name': 'Ueno Station (上野駅)', 'lat': 35.713433, 'lng': 139.77658},
 {'name': 'Urayasu Station (T18) (浦安駅)', 'lat': 35.665743, 'lng': 139.892937},
 {'name': 'Tsukishima Station (月島駅)', 'lat': 35.664021, 'lng': 139.783931},
 {'name': 'Shintomicho Station (Y20) (新富町駅)',
  'lat': 35.670583,
  'lng': 139.773583},
 {'name': 'Bakuro-yokoyama Station (S09) (馬喰横山

In [29]:
train_d = pd.DataFrame(train)

In [30]:
train_d.to_csv("train.csv", index=False)

# Specify the folder path and filename for the CSV file
folder_path = "/Users/usuari/Desktop/Ironhack/BOOTCAMP/projects/project-3/data"
file_name = "train.csv"

# Combine the folder path and filename to create the full file path
full_file_path = f"{folder_path}/{file_name}"

# Export the DataFrame to the specified folder
train_d.to_csv(full_file_path, index=False)

In [31]:
# Create a base map centered around Tokyo, Japan
m = Map(location=[35.652832, 139.839478], zoom_start=13)

# Add Starbucks locations to the map
for location in starbucks:
    tooltip = location['name']
    icon = folium.Icon(color='green', icon_color='white', icon='coffee', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)


for index, row in tok_df.iterrows():
    tooltip = row['name']  # Move the tooltip line inside the loop
    icon = folium.Icon(color='red', icon_color='black', icon='gamepad', prefix='fa')
    folium.Marker(
        location=[row['lat'], row['lon']],
        tooltip=tooltip,  # Set the tooltip for the marker
        icon=icon  # Set the custom icon for the marker
    ).add_to(m)

for location in dog:
    tooltip = location['name']
    icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
for location in train:
    tooltip = location['name']
    icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Display the map
m

### 8. Tokyo's airports

In [32]:
# Tokyo only has two airports.
# Narita airport's coordinates:

lati = 35.770178
longi = 140.3817412

In [33]:
# Haneda airport's coordinates:

latu = 35.5493932
longu = 139.7772583

In [34]:
# Create a base map centered around Tokyo, Japan
m = folium.Map(location=[35.652832, 139.839478], zoom_start=13)

# Add the narita marker
icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
narita.add_to(m)

# Add the haneda marker
icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
haneda.add_to(m)

# Add Starbucks locations to the map
for location in starbucks:
    tooltip = location['name']
    icon = folium.Icon(color='green', icon_color='white', icon='coffee', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Add other markers from tok_df to the map
for index, row in tok_df.iterrows():
    tooltip = row['name']
    icon = folium.Icon(color='red', icon_color='black', icon='gamepad', prefix='fa')
    folium.Marker(
        location=[row['lat'], row['lon']],
        tooltip=tooltip,
        icon=icon
    ).add_to(m)
    
# Add the pet grooming places    
for location in dog:
    tooltip = location['name']
    icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Add the train stations   
for location in train:
    tooltip = location['name']
    icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Display the map
m

### 9. Tokyo's karaokes

In [35]:
venue = "karaoke"
kara = foursquare_places(venue, token, latitude=35.652832, longitude=139.839478, limit=50)
kara

[{'name': 'マハー KARAOKE', 'lat': 35.733583, 'lng': 139.72783},
 {'name': 'Karaoke Rainbow (カラオケレインボー)', 'lat': 35.661554, 'lng': 139.700541},
 {'name': '1Kara (ワンカラ 新宿大ガード店)', 'lat': 35.694082, 'lng': 139.699301},
 {'name': 'Karaoke & Bar Ribbon 2号店', 'lat': 35.694005, 'lng': 139.704074},
 {'name': 'カラオケ館秋葉原店', 'lat': 35.699271, 'lng': 139.77512},
 {'name': 'Pasela Resorts (パセラリゾーツ 秋葉原電気街店)',
  'lat': 35.698971,
  'lng': 139.771662},
 {'name': 'PLEASURE', 'lat': 35.655243, 'lng': 139.698059},
 {'name': 'KARAOKE BOSSANOVA', 'lat': 35.655867, 'lng': 139.65434},
 {'name': 'Pasela Resorts Grande 渋谷', 'lat': 35.661195, 'lng': 139.700246},
 {'name': '歌広場新宿5号店', 'lat': 35.693477, 'lng': 139.703796},
 {'name': 'カラオケ ベスト10 武蔵小山店', 'lat': 35.617547, 'lng': 139.706719},
 {'name': 'アメリカンスタジアム', 'lat': 35.623001, 'lng': 139.609324},
 {'name': '円盤', 'lat': 35.661491, 'lng': 139.723844},
 {'name': 'JOYSOUND 品川港南口店', 'lat': 35.62848, 'lng': 139.743011},
 {'name': 'ジョイサウンド JOYSOUND 池袋西口公園前店', 'lat': 35.

In [36]:
kara_d = pd.DataFrame(kara)

In [37]:
kara_d.to_csv("kara.csv", index=False)

# Specify the folder path and filename for the CSV file
folder_path = "/Users/usuari/Desktop/Ironhack/BOOTCAMP/projects/project-3/data"
file_name = "kara.csv"

# Combine the folder path and filename to create the full file path
full_file_path = f"{folder_path}/{file_name}"

# Export the DataFrame to the specified folder
kara_d.to_csv(full_file_path, index=False)

In [38]:
# Create a base map centered around Tokyo, Japan
m = folium.Map(location=[35.652832, 139.839478], zoom_start=13)

# Add the narita marker
icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
narita.add_to(m)

# Add the haneda marker
icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
haneda.add_to(m)

# Add Starbucks locations to the map
for location in starbucks:
    tooltip = location['name']
    icon = folium.Icon(color='green', icon_color='white', icon='coffee', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Add other markers from tok_df to the map
for index, row in tok_df.iterrows():
    tooltip = row['name']
    icon = folium.Icon(color='red', icon_color='black', icon='gamepad', prefix='fa')
    folium.Marker(
        location=[row['lat'], row['lon']],
        tooltip=tooltip,
        icon=icon
    ).add_to(m)
    
# Add the pet grooming places    
for location in dog:
    tooltip = location['name']
    icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Add the train stations   
for location in train:
    tooltip = location['name']
    icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
# Add the karaokes so that the employees can have fun

for location in kara:
    tooltip = location['name']
    icon = folium.Icon(color='black', icon_color='white', icon='microphone', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Display the map
m

### 10. Vegan places for the CEO

In [39]:
venue = "vegan"
veg = foursquare_places(venue, token, latitude=35.652832, longitude=139.839478, limit=50)
veg

[{'name': 'Veg Kitchen (ベジキッチン)', 'lat': 35.705573, 'lng': 139.777804},
 {'name': "Olu'olu Cafe", 'lat': 35.644288, 'lng': 139.679708},
 {'name': 'Vege Herb Saga (ヴェジハーブサーガ)', 'lat': 35.70609, 'lng': 139.775354},
 {'name': 'meu nota', 'lat': 35.70332, 'lng': 139.647871},
 {'name': 'Soranoiro (ソラノイロ)', 'lat': 35.683036, 'lng': 139.73936},
 {'name': 'Alaska zwei', 'lat': 35.648953, 'lng': 139.69105},
 {'name': 'Milan Nataraj (ミラン・ナタラジ)', 'lat': 35.6611, 'lng': 139.701062},
 {'name': 'Kuumba du Falafel', 'lat': 35.657162, 'lng': 139.690826},
 {'name': 'Mr. FARMER', 'lat': 35.628129, 'lng': 139.656741},
 {'name': 'KOMEDA is □', 'lat': 35.667978, 'lng': 139.769418},
 {'name': 'BERG', 'lat': 35.691338, 'lng': 139.701123},
 {'name': 'kokonn (Kokonn)', 'lat': 35.723471, 'lng': 139.768703},
 {'name': 'FIRE HOUSE', 'lat': 35.707565, 'lng': 139.758191},
 {'name': 'No.4', 'lat': 35.688226, 'lng': 139.736152},
 {'name': 'Tokyo Shiba Tofuya Ukai (東京芝 とうふ屋うかい)',
  'lat': 35.657583,
  'lng': 139.74510

In [40]:
veg_d = pd.DataFrame(veg)

In [41]:
veg_d.to_csv("veg.csv", index=False)

# Specify the folder path and filename for the CSV file
folder_path = "/Users/usuari/Desktop/Ironhack/BOOTCAMP/projects/project-3/data"
file_name = "veg.csv"

# Combine the folder path and filename to create the full file path
full_file_path = f"{folder_path}/{file_name}"

# Export the DataFrame to the specified folder
veg_d.to_csv(full_file_path, index=False)

In [42]:
# Create a base map centered around Tokyo, Japan
m = folium.Map(location=[35.652832, 139.839478], zoom_start=13)

# Add the narita marker
icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
narita.add_to(m)

# Add the haneda marker
icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
haneda.add_to(m)

# Add Starbucks locations to the map
for location in starbucks:
    tooltip = location['name']
    icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Add other markers from tok_df to the map
for index, row in tok_df.iterrows():
    tooltip = row['name']
    icon = folium.Icon(color='purple', icon_color='white', icon='gamepad', prefix='fa')
    folium.Marker(
        location=[row['lat'], row['lon']],
        tooltip=tooltip,
        icon=icon
    ).add_to(m)
    
# Add the pet grooming places    
for location in dog:
    tooltip = location['name']
    icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Add the train stations   
for location in train:
    tooltip = location['name']
    icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
# Add the karaokes so that the employees can have fun

for location in kara:
    tooltip = location['name']
    icon = folium.Icon(color='black', icon_color='white', icon='microphone', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
for location in veg:
    tooltip = location['name']
    icon = folium.Icon(color='green', icon_color='white', icon='leaf', prefix='fa')
    folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

# Display the map
m

/var/folders/_b/4s7pp99j1qq9lxsqpjphc78m0000gn/T/ipykernel_83833/3017990445.py:17: UserWarning: color argument of Icon should be one of: {'lightgreen', 'darkgreen', 'pink', 'gray', 'green', 'lightgray', 'darkblue', 'white', 'black', 'purple', 'blue', 'beige', 'darkred', 'cadetblue', 'red', 'lightred', 'lightblue', 'orange', 'darkpurple'}.
  icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')


### 11. Tokyo's successful tech startups: 

#### I'm going to check which companies have raised at least 1 million dollars in tokyo.

In [43]:
filters = {"total_money_raised":{"$regex":'M'}, "offices.city": "Tokyo"}

projection = {'name': 1, '_id': 0, 'offices': 1, 'number_of_employees': 1, 'category_code': 1, 'tag_list': 1, 'total_money_raised': 1}

startups = list(c.find(filters, projection).sort('total_money_raised', -1))

In [44]:
# Extract the relevant information from the nested structure
startups_df = []
for entry in startups:
    name = entry['name']
    employees = entry['number_of_employees']
    tag = entry['tag_list']
    category_code = entry['category_code']
    for office in entry['offices']:
        description = office.get('description', '')
        address1 = office.get('address1', '')
        address2 = office.get('address2', '')
        zip_code = office.get('zip_code', '')
        city = office.get('city', '')
        lat = office.get('latitude', '')
        lon = office.get('longitude', '')
        country_code = office.get('country_code', '')
        startups_df.append([name, category_code, description, employees, tag, address1, address2, zip_code, city, country_code, lat, lon])

# Create the DataFrame
columns = ['name', 'category_code', 'description', 'employees', 'tag', 'address1', 'address2', 'zip_code', 'city', 'country_code', 'lat', 'lon']
startups_df = pd.DataFrame(startups_df, columns=columns)

# Display the DataFrame
startups_df

name category_code      description  employees  \
0        Nexway     ecommerce        Nexway HQ      160.0   
1        Nexway     ecommerce  Nexway Services      160.0   
2        Nexway     ecommerce        Nexway UK      160.0   
3        Nexway     ecommerce   Nexway Benelux      160.0   
4        Nexway     ecommerce      Nexway Gmbh      160.0   
..          ...           ...              ...        ...   
181  Brightcove    enterprise                       220.0   
182  Brightcove    enterprise                       220.0   
183  Brightcove    enterprise                       220.0   
184  Brightcove    enterprise                       220.0   
185  Brightcove    enterprise                       220.0   

                                                   tag  \
0    esd, e-commerce, software, download, video-gam...   
1    esd, e-commerce, software, download, video-gam...   
2    esd, e-commerce, software, download, video-gam...   
3    esd, e-commerce, software, download, video-gam...   
4    esd, e-commerce, software, download, video-gam...   
..                                                 ...   
181  brightcove, online-video-platform, video, tv-e...   
182  brightcove, online-video-platform, video, tv-e...   
183  brightcove, online-video-platform, video, tv-e...   
184  brightcove, online-video-platform, video, tv-e...   
185  brightcove, online-video-platform, video, tv-e...   

                        address1             address2  zip_code  \
0               1 bd des Bouvets                          92741   
1            1 bd Amiral Courbet             CS 70002     30020   
2    Unit 12, Westbourne Studios      242 Acklam Road   W10 5JJ   
3          ChaussÃ©e d'Alsemberg           995 Bte 19      1180   
4        Hanauer Landstrasse 146                          60314   
..                           ...                  ...       ...   
181                708 Third Ave  6th Floor, Suite 30     10017   
182       200 West Mercer Street            Suite 204     98119   
183             53 Chandos Place        Covent Garden  WC2N 4HS   
184             StadthausbrÃ¼cke                        D-22355   
185         Avenida Diagonal 640             planta 6     08017   

               city country_code        lat       lon  
0    Nanterre cedex          FRA  48.898044  2.220001  
1      NÃ®mes cedex          FRA  43.837967  4.363104  
2            London          GBR        NaN       NaN  
3          Brussels          BEL  50.796848  4.335846  
4         Frankfurt          DEU        NaN       NaN  
..              ...          ...        ...       ...  
181        New York          USA        NaN       NaN  
182         Seattle          USA        NaN       NaN  
183          London          GBR        NaN       NaN  
184         Hamburg          DEU        NaN       NaN  
185       Barcelona          ESP        NaN       NaN  

[186 rows x 12 columns]

In [45]:
desired_value = 'Tokyo'
startups_df = startups_df[startups_df['city'] == desired_value]
startups_df

name    category_code                description  \
8                    Nexway        ecommerce      Degica / Boonty Japan   
13                     GREE      games_video               Headquarters   
16                SolarEdge        cleantech         Local Japan Office   
21   Chelsio Communications  network_hosting                              
26                    OpenX      advertising                      Tokyo   
32               ReachLocal      advertising          Asia Headquarters   
36               Proofpoint         software                              
70                   Google           search  Google Japan Headquarters   
105       UQ Communications           mobile               Headquarters   
106                 Rakuten              web                Headquarter   
107                  eriQoo           search               Tokyo Office   
112                  Corvil            other                      Tokyo   
125                  hybris       enterprise               Japan Office   
135      Basho Technologies         software                Basho Japan   
137                   Ecrio           mobile            Japanese Office   
143                  Nexsan         hardware                      Japan   
144               Six Apart       enterprise                  Global HQ   
149                  InMobi           mobile                      Tokyo   
160                   Icera           mobile                Icera Tokyo   
162                   Gengo              web                      Tokyo   
164               Tonchidot           mobile                         HQ   
165               Tonchidot           mobile                         HQ   
172          Opera Software         software                      Tokyo   
180              Brightcove       enterprise         Japan Headquarters   

     employees                                                tag  \
8        160.0  esd, e-commerce, software, download, video-gam...   
13       700.0  mobile-web, japan, tokyo, social-network, mobi...   
16       230.0  solar-power-harvesting, photovoltaic, power-op...   
21       170.0                                                      
26       305.0  ad-server, ad-serving, ad-exchange, yield-opti...   
32      1700.0  internet-marketing, online-advertising, web-pr...   
36         NaN                    email-security, email-archiving   
70     28000.0  search, gmail, blogger, find, information, you...   
105      222.0  mobile-broadband, wimax, japan, intel-capital,...   
106    10000.0  ecommerce, japan, global, internet-services, p...   
107       96.0                                     search-engines   
112      100.0                                                      
125        NaN                                                      
135      110.0  database, datastore, open-source, nosql, appli...   
137        NaN                                               None   
143      126.0  green-storage, energy-efficient-storage, disk-...   
144       50.0                                      blogging, cms   
149      900.0  mobile, ads, mobile-ad-network, ad-network, mo...   
160      260.0  wireless-communication, cellular-broadbands, s...   
162       38.0  translation-services, english, japanese, crowd...   
164       20.0  techcrunch50, tc50, iphone, mobile, ar, augmen...   
165       20.0  techcrunch50, tc50, iphone, mobile, ar, augmen...   
172        NaN                                                      
180      220.0  brightcove, online-video-platform, video, tv-e...   

                                              address1  \
8                                 TK Kichojijo Bldg 6F   
13         Roppongi-Hills Mori Tower, 6-10-1, Roppongi   
16   B-9 Ariake Frontier Building, 3-7-26 Ariake, K...   
21                                  SHIMA Akasaka Bldg   
26                                4-12-25 Minami-Azabu   
32                           Ark Yagi Hills 10F, 1-8-7   
36             

In [46]:
# I'm going to drop GREE, because we already have it as a videogame company. 

specific_value = 'GREE'

# Use the drop method to remove rows with the specific value
startups_df = startups_df[startups_df['name'] != specific_value]
startups_df

name    category_code                description  \
8                    Nexway        ecommerce      Degica / Boonty Japan   
16                SolarEdge        cleantech         Local Japan Office   
21   Chelsio Communications  network_hosting                              
26                    OpenX      advertising                      Tokyo   
32               ReachLocal      advertising          Asia Headquarters   
36               Proofpoint         software                              
70                   Google           search  Google Japan Headquarters   
105       UQ Communications           mobile               Headquarters   
106                 Rakuten              web                Headquarter   
107                  eriQoo           search               Tokyo Office   
112                  Corvil            other                      Tokyo   
125                  hybris       enterprise               Japan Office   
135      Basho Technologies         software                Basho Japan   
137                   Ecrio           mobile            Japanese Office   
143                  Nexsan         hardware                      Japan   
144               Six Apart       enterprise                  Global HQ   
149                  InMobi           mobile                      Tokyo   
160                   Icera           mobile                Icera Tokyo   
162                   Gengo              web                      Tokyo   
164               Tonchidot           mobile                         HQ   
165               Tonchidot           mobile                         HQ   
172          Opera Software         software                      Tokyo   
180              Brightcove       enterprise         Japan Headquarters   

     employees                                                tag  \
8        160.0  esd, e-commerce, software, download, video-gam...   
16       230.0  solar-power-harvesting, photovoltaic, power-op...   
21       170.0                                                      
26       305.0  ad-server, ad-serving, ad-exchange, yield-opti...   
32      1700.0  internet-marketing, online-advertising, web-pr...   
36         NaN                    email-security, email-archiving   
70     28000.0  search, gmail, blogger, find, information, you...   
105      222.0  mobile-broadband, wimax, japan, intel-capital,...   
106    10000.0  ecommerce, japan, global, internet-services, p...   
107       96.0                                     search-engines   
112      100.0                                                      
125        NaN                                                      
135      110.0  database, datastore, open-source, nosql, appli...   
137        NaN                                               None   
143      126.0  green-storage, energy-efficient-storage, disk-...   
144       50.0                                      blogging, cms   
149      900.0  mobile, ads, mobile-ad-network, ad-network, mo...   
160      260.0  wireless-communication, cellular-broadbands, s...   
162       38.0  translation-services, english, japanese, crowd...   
164       20.0  techcrunch50, tc50, iphone, mobile, ar, augmen...   
165       20.0  techcrunch50, tc50, iphone, mobile, ar, augmen...   
172        NaN                                                      
180      220.0  brightcove, online-video-platform, video, tv-e...   

                                              address1  \
8                                 TK Kichojijo Bldg 6F   
16   B-9 Ariake Frontier Building, 3-7-26 Ariake, K...   
21                                  SHIMA Akasaka Bldg   
26                                4-12-25 Minami-Azabu   
32                           Ark Yagi Hills 10F, 1-8-7   
36                     BUREX Kojimachi Kojimachi 3-5-2   
70                                   6F Cerulean Tower   
105                           Shinagawa East One Tower   
106     Rakuten Tower, Shinagawa Seaside Ra

In [47]:
# I'm going to try this function and see if it extracts some coordina

def geocode_addresses():
    geolocator = Nominatim(user_agent="your_app_name")

    for index, row in startups_df.iterrows():
        address = row['address1']
        location = geolocator.geocode(address)

        if location is not None:
            startups_df.at[index, 'lat'] = location.latitude
            startups_df.at[index, 'lon'] = location.longitude

        # Add a sleep to avoid hitting the geocoding service too quickly
        time.sleep(10)  

    return startups_df

In [48]:
geocode_addresses()

Retrying (Retry(total=1, connect=None, read=None, redirect=None, status=None)) after connection broken by 'ReadTimeoutError("HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Read timed out. (read timeout=1)")': /search?q=2-5-12%2C+Shinjuku&format=json&limit=1


name    category_code                description  \
8                    Nexway        ecommerce      Degica / Boonty Japan   
16                SolarEdge        cleantech         Local Japan Office   
21   Chelsio Communications  network_hosting                              
26                    OpenX      advertising                      Tokyo   
32               ReachLocal      advertising          Asia Headquarters   
36               Proofpoint         software                              
70                   Google           search  Google Japan Headquarters   
105       UQ Communications           mobile               Headquarters   
106                 Rakuten              web                Headquarter   
107                  eriQoo           search               Tokyo Office   
112                  Corvil            other                      Tokyo   
125                  hybris       enterprise               Japan Office   
135      Basho Technologies         software                Basho Japan   
137                   Ecrio           mobile            Japanese Office   
143                  Nexsan         hardware                      Japan   
144               Six Apart       enterprise                  Global HQ   
149                  InMobi           mobile                      Tokyo   
160                   Icera           mobile                Icera Tokyo   
162                   Gengo              web                      Tokyo   
164               Tonchidot           mobile                         HQ   
165               Tonchidot           mobile                         HQ   
172          Opera Software         software                      Tokyo   
180              Brightcove       enterprise         Japan Headquarters   

     employees                                                tag  \
8        160.0  esd, e-commerce, software, download, video-gam...   
16       230.0  solar-power-harvesting, photovoltaic, power-op...   
21       170.0                                                      
26       305.0  ad-server, ad-serving, ad-exchange, yield-opti...   
32      1700.0  internet-marketing, online-advertising, web-pr...   
36         NaN                    email-security, email-archiving   
70     28000.0  search, gmail, blogger, find, information, you...   
105      222.0  mobile-broadband, wimax, japan, intel-capital,...   
106    10000.0  ecommerce, japan, global, internet-services, p...   
107       96.0                                     search-engines   
112      100.0                                                      
125        NaN                                                      
135      110.0  database, datastore, open-source, nosql, appli...   
137        NaN                                               None   
143      126.0  green-storage, energy-efficient-storage, disk-...   
144       50.0                                      blogging, cms   
149      900.0  mobile, ads, mobile-ad-network, ad-network, mo...   
160      260.0  wireless-communication, cellular-broadbands, s...   
162       38.0  translation-services, english, japanese, crowd...   
164       20.0  techcrunch50, tc50, iphone, mobile, ar, augmen...   
165       20.0  techcrunch50, tc50, iphone, mobile, ar, augmen...   
172        NaN                                                      
180      220.0  brightcove, online-video-platform, video, tv-e...   

                                              address1  \
8                                 TK Kichojijo Bldg 6F   
16   B-9 Ariake Frontier Building, 3-7-26 Ariake, K...   
21                                  SHIMA Akasaka Bldg   
26                                4-12-25 Minami-Azabu   
32                           Ark Yagi Hills 10F, 1-8-7   
36                     BUREX Kojimachi Kojimachi 3-5-2   
70                                   6F Cerulean Tower   
105                           Shinagawa East One Tower   
106     Rakuten Tower, Shinagawa Seaside Ra

In [49]:
startups_df.to_csv("startups.csv", index=True)
folder_path = "/Users/usuari/Desktop/Ironhack/BOOTCAMP/projects/project-3/data"
file_name = "startups.csv"

full_file_path = f"{folder_path}/{file_name}"
startups_df.to_csv(full_file_path, index=True)

In [50]:
def semi_final_map():
    
    # Create a base map centered around Tokyo, Japan
    m = folium.Map(location=[35.652832, 139.839478], zoom_start=13)

    # Add the narita marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
    narita.add_to(m)

    # Add the haneda marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
    haneda.add_to(m)

    # Add Starbucks locations to the map
    for location in starbucks:
        tooltip = location['name']
        icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add other markers from tok_df to the map
    for index, row in tok_df.iterrows():
        tooltip = row['name']
        icon = folium.Icon(color='purple', icon_color='white', icon='gamepad', prefix='fa')
        folium.Marker(location=[row['lat'], row['lon']], tooltip=tooltip, icon=icon).add_to(m)
    

    # Add the successful tech startups that have coordinates    
    for index, row in startups_df.iterrows():
        if not pd.isna(row['lat']) and not pd.isna(row['lon']):
            tooltip = row['name']
            icon = folium.Icon(color='red', icon_color='white', icon='cloud-upload', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lon']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
          
    # Add the pet grooming places    
    for location in dog:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add the train stations   
    for location in train:
        tooltip = location['name']
        icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    # Add the karaokes so that the employees can have fun

    for location in kara:
        tooltip = location['name']
        icon = folium.Icon(color='black', icon_color='white', icon='microphone', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    for location in veg:
        tooltip = location['name']
        icon = folium.Icon(color='green', icon_color='white', icon='leaf', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    return m

In [51]:
semi_final_map()

/var/folders/_b/4s7pp99j1qq9lxsqpjphc78m0000gn/T/ipykernel_83833/4229406767.py:19: UserWarning: color argument of Icon should be one of: {'lightgreen', 'darkgreen', 'pink', 'gray', 'green', 'lightgray', 'darkblue', 'white', 'black', 'purple', 'blue', 'beige', 'darkred', 'cadetblue', 'red', 'lightred', 'lightblue', 'orange', 'darkpurple'}.
  icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')


In [52]:
def circle_map():
    
    # Create a base map centered around Tokyo, Japan
    m = folium.Map(location=[35.652832, 139.839478], zoom_start=13)

    # Add the narita marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
    narita.add_to(m)

    # Add the haneda marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
    haneda.add_to(m)

    # Add Starbucks locations to the map
    for location in starbucks:
        tooltip = location['name']
        icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add other markers from tok_df to the map
    for index, row in tok_df.iterrows():
        tooltip = row['name']
        icon = folium.Icon(color='purple', icon_color='white', icon='gamepad', prefix='fa')
        folium.Marker(location=[row['lat'], row['lon']], tooltip=tooltip, icon=icon).add_to(m)
    

    # Add the successful tech startups that have coordinates    
    for index, row in startups_df.iterrows():
        if not pd.isna(row['lat']) and not pd.isna(row['lon']):
            tooltip = row['name']
            icon = folium.Icon(color='red', icon_color='white', icon='cloud-upload', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lon']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
          
    # Add the pet grooming places    
    for location in dog:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add the train stations   
    for location in train:
        tooltip = location['name']
        icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    # Add the karaokes so that the employees can have fun

    for location in kara:
        tooltip = location['name']
        icon = folium.Icon(color='black', icon_color='white', icon='microphone', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    for location in veg:
        tooltip = location['name']
        icon = folium.Icon(color='green', icon_color='white', icon='leaf', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
        
        
    # Add circles with a ratio of the closest things
    circle_center = [35.6555691, 139.7343113] # I have chosen this center because it's a dog grooming place that it's nearby to all the things required.
    circle_radius = 1000 
    circle_radius_2 = 1500

    # Create a circle with the specified center and radius
    folium.Circle(location=circle_center, radius=circle_radius, color='red', fill=True, fill_color='red', fill_opacity=0.2).add_to(m)
    folium.Circle(location=circle_center, radius=circle_radius_2, color='blue', fill=True, fill_color='red', fill_opacity=0.2).add_to(m)

    return m

In [53]:
map = circle_map()
map.save('circle_map.html')
map

/var/folders/_b/4s7pp99j1qq9lxsqpjphc78m0000gn/T/ipykernel_83833/2376457566.py:19: UserWarning: color argument of Icon should be one of: {'lightgreen', 'darkgreen', 'pink', 'gray', 'green', 'lightgray', 'darkblue', 'white', 'black', 'purple', 'blue', 'beige', 'darkred', 'cadetblue', 'red', 'lightred', 'lightblue', 'orange', 'darkpurple'}.
  icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')


In [54]:
##### Para tomar la decision
# 1. Hacer circulos con folium.Circle() por cada empresa con X radio

In [55]:
start_ups = pd.read_csv("/Users/usuari/Desktop/Ironhack/BOOTCAMP/projects/project-3/data/startups.csv")
start_ups

Unnamed: 0                    name    category_code  \
0            8                  Nexway        ecommerce   
1           16               SolarEdge        cleantech   
2           21  Chelsio Communications  network_hosting   
3           26                   OpenX      advertising   
4           32              ReachLocal      advertising   
5           36              Proofpoint         software   
6           70                  Google           search   
7          105       UQ Communications           mobile   
8          106                 Rakuten              web   
9          107                  eriQoo           search   
10         112                  Corvil            other   
11         125                  hybris       enterprise   
12         135      Basho Technologies         software   
13         137                   Ecrio           mobile   
14         143                  Nexsan         hardware   
15         144               Six Apart       enterprise   
16         149                  InMobi           mobile   
17         160                   Icera           mobile   
18         162                   Gengo              web   
19         164               Tonchidot           mobile   
20         165               Tonchidot           mobile   
21         172          Opera Software         software   
22         180              Brightcove       enterprise   

                  description  employees  \
0       Degica / Boonty Japan      160.0   
1          Local Japan Office      230.0   
2                         NaN      170.0   
3                       Tokyo      305.0   
4           Asia Headquarters     1700.0   
5                         NaN        NaN   
6   Google Japan Headquarters    28000.0   
7                Headquarters      222.0   
8                 Headquarter    10000.0   
9                Tokyo Office       96.0   
10                      Tokyo      100.0   
11               Japan Office        NaN   
12                Basho Japan      110.0   
13            Japanese Office        NaN   
14                      Japan      126.0   
15                  Global HQ       50.0   
16                      Tokyo      900.0   
17                Icera Tokyo      260.0   
18                      Tokyo       38.0   
19                         HQ       20.0   
20                         HQ       20.0   
21                      Tokyo        NaN   
22         Japan Headquarters      220.0   

                                                  tag  \
0   esd, e-commerce, software, download, video-gam...   
1   solar-power-harvesting, photovoltaic, power-op...   
2                                                 NaN   
3   ad-server, ad-serving, ad-exchange, yield-opti...   
4   internet-marketing, online-advertising, web-pr...   
5                     email-security, email-archiving   
6   search, gmail, blogger, find, information, you...   
7   mobile-broadband, wimax, japan, intel-capital,...   
8   ecommerce, japan, global, internet-services, p...   
9                                      search-engines   
10                                                NaN   
11                                                NaN   
12  database, datastore, open-source, nosql, appli...   
13                                                NaN   
14  green-storage, energy-efficient-storage, disk-...   
15                                      blogging, cms   
16  mobile, ads, mobile-ad-network, ad-network, mo...   
17  wireless-communication, cellular-broadbands, s...   
18  translation-services, english, japanese, crowd...   
19  techcrunch50, tc50, iphone, mobile, ar, augmen...   
20  techcrunch50, tc50, iphone, mobile, ar, augmen...   
21                                                NaN   
22  brightcove, online-video-platform, video, tv-e...   

                                             address1  \
0                                TK Kichojijo Bldg 6F   
1   B-9 Ariake Frontier Building, 3-7-26 Ariake

In [56]:
start = start_ups.dropna(subset=["lat"])
start

Unnamed: 0                    name    category_code  \
2           21  Chelsio Communications  network_hosting   
6           70                  Google           search   
7          105       UQ Communications           mobile   
9          107                  eriQoo           search   
10         112                  Corvil            other   
15         144               Six Apart       enterprise   
19         164               Tonchidot           mobile   
20         165               Tonchidot           mobile   

                  description  employees  \
2                         NaN      170.0   
6   Google Japan Headquarters    28000.0   
7                Headquarters      222.0   
9                Tokyo Office       96.0   
10                      Tokyo      100.0   
15                  Global HQ       50.0   
19                         HQ       20.0   
20                         HQ       20.0   

                                                  tag  \
2                                                 NaN   
6   search, gmail, blogger, find, information, you...   
7   mobile-broadband, wimax, japan, intel-capital,...   
9                                      search-engines   
10                                                NaN   
15                                      blogging, cms   
19  techcrunch50, tc50, iphone, mobile, ar, augmen...   
20  techcrunch50, tc50, iphone, mobile, ar, augmen...   

                    address1                          address2  zip_code  \
2         SHIMA Akasaka Bldg                         Minato-ku  107-0052   
6          6F Cerulean Tower              26-1 Sakuragaoka-cho  150-8512   
7   Shinagawa East One Tower          2-16-1 Konan,  Minato-ku  108-0075   
9          Roppongi 4-4-3-33                               NaN  106-0032   
10    Yurakucho ITOCiA 2-7-1              Yurakucho Chiyoda-ku  100-0006   
15            5-2-39 Akasaka  7th Floor, Entsuji Gadelius Bldg  107-0052   
19          2-5-12, Shinjuku                       Shinjuku-ku  160-0022   
20          2-5-12, Shinjuku                       Shinjuku-ku  160-0022   

     city country_code        lat         lon  
2   Tokyo          JPN  35.669185  139.734548  
6   Tokyo          JPN  35.657591  139.699055  
7   Tokyo          JPN  35.627796  139.740745  
9   Tokyo          JPN  35.661512  139.728418  
10  Tokyo          JPN  35.673578  139.764248  
15  Tokyo          JPN  35.673165  139.738309  
19  Tokyo          JPN  35.693763  139.703632  
20  Tokyo          JPN  35.693763  139.703632

In [57]:
start = start.drop(20)
start

Unnamed: 0                    name    category_code  \
2           21  Chelsio Communications  network_hosting   
6           70                  Google           search   
7          105       UQ Communications           mobile   
9          107                  eriQoo           search   
10         112                  Corvil            other   
15         144               Six Apart       enterprise   
19         164               Tonchidot           mobile   

                  description  employees  \
2                         NaN      170.0   
6   Google Japan Headquarters    28000.0   
7                Headquarters      222.0   
9                Tokyo Office       96.0   
10                      Tokyo      100.0   
15                  Global HQ       50.0   
19                         HQ       20.0   

                                                  tag  \
2                                                 NaN   
6   search, gmail, blogger, find, information, you...   
7   mobile-broadband, wimax, japan, intel-capital,...   
9                                      search-engines   
10                                                NaN   
15                                      blogging, cms   
19  techcrunch50, tc50, iphone, mobile, ar, augmen...   

                    address1                          address2  zip_code  \
2         SHIMA Akasaka Bldg                         Minato-ku  107-0052   
6          6F Cerulean Tower              26-1 Sakuragaoka-cho  150-8512   
7   Shinagawa East One Tower          2-16-1 Konan,  Minato-ku  108-0075   
9          Roppongi 4-4-3-33                               NaN  106-0032   
10    Yurakucho ITOCiA 2-7-1              Yurakucho Chiyoda-ku  100-0006   
15            5-2-39 Akasaka  7th Floor, Entsuji Gadelius Bldg  107-0052   
19          2-5-12, Shinjuku                       Shinjuku-ku  160-0022   

     city country_code        lat         lon  
2   Tokyo          JPN  35.669185  139.734548  
6   Tokyo          JPN  35.657591  139.699055  
7   Tokyo          JPN  35.627796  139.740745  
9   Tokyo          JPN  35.661512  139.728418  
10  Tokyo          JPN  35.673578  139.764248  
15  Tokyo          JPN  35.673165  139.738309  
19  Tokyo          JPN  35.693763  139.703632

In [58]:
start.to_csv("start.csv", index=False)

folder_path = "/Users/usuari/Desktop/Ironhack/BOOTCAMP/projects/project-3/data"
file_name = "start.csv"

# Combine the folder path and filename to create the full file path
full_file_path = f"{folder_path}/{file_name}"

# Export the DataFrame to the specified folder
start.to_csv(full_file_path, index=False)

In [59]:
def circle_map1():
    
    # Create a base map centered around Tokyo, Japan
    m = folium.Map(location=[35.652832, 139.839478], zoom_start=13)

    # Add the narita marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
    narita.add_to(m)

    # Add the haneda marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
    haneda.add_to(m)

    # Add Starbucks locations to the map
    for location in starbucks:
        tooltip = location['name']
        icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add other markers from tok_df to the map
    for index, row in tok_df.iterrows():
        tooltip = row['name']
        icon = folium.Icon(color='purple', icon_color='white', icon='gamepad', prefix='fa')
        folium.Marker(location=[row['lat'], row['lon']], tooltip=tooltip, icon=icon).add_to(m)
    

    # Add the successful tech startups that have coordinates    
    for index, row in start.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='red', icon_color='white', icon='cloud-upload', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lon']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
          
    # Add the pet grooming places    
    for location in dog:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add the train stations   
    for location in train:
        tooltip = location['name']
        icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    # Add the karaokes so that the employees can have fun

    for location in kara:
        tooltip = location['name']
        icon = folium.Icon(color='black', icon_color='white', icon='microphone', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    for location in veg:
        tooltip = location['name']
        icon = folium.Icon(color='green', icon_color='white', icon='leaf', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
        
        
    # Add circles with a ratio of the closest things
    
    circles = [
        {"center": [35.669185, 139.734548], "radius": 800, "color": "red",},
        {"center": [35.657591, 139.699055], "radius": 800, "color": "blue"},
        {"center": [35.627796, 139.740745], "radius": 800, "color": "green"},
        {"center": [35.661512, 139.728418], "radius": 800, "color": "orange"},
        {"center": [35.673578, 139.764248], "radius": 800, "color": "purple"},
        {"center": [35.673165, 139.738309], "radius": 800, "color": "yellow"},
        {"center": [35.693763, 139.703632], "radius": 800, "color": "gray"}
        
    ]

    for circle_info in circles:
        circle_center = circle_info["center"]
        circle_radius = circle_info["radius"]
        circle_color = circle_info["color"]

        folium.Circle(
            location=circle_center,
            radius=circle_radius,
            color=circle_color,
            fill=True,
            fill_color=circle_color,
            fill_opacity=0.2
        ).add_to(m)

    return m

In [60]:
circle_map1()

/var/folders/_b/4s7pp99j1qq9lxsqpjphc78m0000gn/T/ipykernel_83833/3911328413.py:19: UserWarning: color argument of Icon should be one of: {'lightgreen', 'darkgreen', 'pink', 'gray', 'green', 'lightgray', 'darkblue', 'white', 'black', 'purple', 'blue', 'beige', 'darkred', 'cadetblue', 'red', 'lightred', 'lightblue', 'orange', 'darkpurple'}.
  icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')


In [61]:
venue = "elementary school"
guardes = foursquare_places(venue, token, latitude=35.652832, longitude=139.839478, limit=50)
guardes

[{'name': '江戸川区立第四葛西小学校', 'lat': 35.658804, 'lng': 139.871097},
 {'name': 'Tokyo Korean Primary School II (東京朝鮮第二初級学校)',
  'lat': 35.656699,
  'lng': 139.804502},
 {'name': 'Minamikasai Elementary School (南葛西小学校)',
  'lat': 35.64665,
  'lng': 139.874473},
 {'name': '江東区立有明小学校', 'lat': 35.640259, 'lng': 139.796104},
 {'name': '江戸川区立西一之江小学校', 'lat': 35.690033, 'lng': 139.873578},
 {'name': '浦安市立見明川小学校', 'lat': 35.639022, 'lng': 139.894583},
 {'name': '江東区立八名川小学校', 'lat': 35.686829, 'lng': 139.795291},
 {'name': '江戸川区立一之江小学校', 'lat': 35.689817, 'lng': 139.880987},
 {'name': '浦安市立東野小学校', 'lat': 35.651029, 'lng': 139.901365},
 {'name': '江戸川区立瑞江小学校', 'lat': 35.685461, 'lng': 139.887028},
 {'name': '月島第二小学校', 'lat': 35.660231, 'lng': 139.77599},
 {'name': '市川市立福栄小学校', 'lat': 35.671742, 'lng': 139.907306},
 {'name': '浦安市立入船南小学校', 'lat': 35.645602, 'lng': 139.912687},
 {'name': '浦安市立美浜北小学校', 'lat': 35.655154, 'lng': 139.914943},
 {'name': '春江小学校', 'lat': 35.699029, 'lng': 139.8938},
 {'name': '

In [62]:
guardes_d = pd.DataFrame(guardes)
guardes_d

name        lat         lng
0                                    江戸川区立第四葛西小学校  35.658804  139.871097
1     Tokyo Korean Primary School II (東京朝鮮第二初級学校)  35.656699  139.804502
2          Minamikasai Elementary School (南葛西小学校)  35.646650  139.874473
3                                       江東区立有明小学校  35.640259  139.796104
4                                    江戸川区立西一之江小学校  35.690033  139.873578
5                                      浦安市立見明川小学校  35.639022  139.894583
6                                      江東区立八名川小学校  35.686829  139.795291
7                                     江戸川区立一之江小学校  35.689817  139.880987
8                                       浦安市立東野小学校  35.651029  139.901365
9                                      江戸川区立瑞江小学校  35.685461  139.887028
10                                        月島第二小学校  35.660231  139.775990
11                                      市川市立福栄小学校  35.671742  139.907306
12                                     浦安市立入船南小学校  35.645602  139.912687
13                                     浦安市立美浜北小学校  35.655154  139.914943
14                                          春江小学校  35.699029  139.893800
15                                       高洲小学校体育館  35.636248  139.917212
16                                          渋江小学校  35.730667  139.842470
17                                       港区立東町小学校  35.650918  139.735776
18                                      市川市立妙典小学校  35.695936  139.929971
19            Hongo Elementary School (文京区立本郷小学校)  35.707978  139.757983
20              Honmura Elementary School (本村小学校)  35.649764  139.729945
21                                    品川区立品川学園中学校  35.617513  139.738439
22                                         浅間台小学校  35.611503  139.736492
23                                       品川区立日野学園  35.624020  139.728609
24                                      文京区立汐見小学校  35.723563  139.760814
25                                      市川市立平田小学校  35.724115  139.918017
26                                    荒川区立第二峡田小学校  35.738581  139.782437
27                                       東京女学館小学校  35.655716  139.717299
28                                       港区立青南小学校  35.662974  139.716227
29                                     葛飾区立上千葉小学校  35.754049  139.838171
30                                          柴又小学校  35.752893  139.877032
31     Tokiwamatsu Elementary School (渋谷区立常磐松小学校)  35.655639  139.710411
32                                      私立青山学院初等部  35.658190  139.709961
33                                          亀青小学校  35.758809  139.852904
34                                          昭和小学校  35.731711  139.749615
35                                    北区立滝野川第七小学校  35.738517  139.753931
36                                      渋谷区立鳩森小学校  35.682352  139.705858
37                Enzan Elementary School (延山小学校)  35.608908  139.708050
38        Daini Enzan Elementary School (第二延山小学校)  35.609978  139.703560
39                                      目黒区立菅刈小学校  35.651821  139.692178
40                                     目黒区立月光原小学校  35.623172  139.694895
41  Takinogawa Daigo Elementary School (滝野川第五小学校)  35.749378  139.749528
42                                  大田区立小学校 - 東糀谷  35.558646  139.744112
43                                      葛飾区立飯塚小学校  35.777093  139.858083
44                                      船橋市立海神小学校  35.703250  139.979468
45                                       目黒区立碑小学校  35.619417  139.691253
46                                      目黒区立原町小学校  35.615814  139.690438
47                                      新宿区立柏木小学校  35.700548  139.689323
48                                      トキワ松学園小学校  35.620710  139.682360
49            Ookayama Elementary School (大岡山小学校)  35.615638  139.683140

In [63]:
guardes_d.to_csv("guardes.csv", index=False)

# Specify the folder path and filename for the CSV file
folder_path = "/Users/usuari/Desktop/Ironhack/BOOTCAMP/projects/project-3/data"
file_name = "guardes.csv"

# Combine the folder path and filename to create the full file path
full_file_path = f"{folder_path}/{file_name}"

# Export the DataFrame to the specified folder
guardes_d.to_csv(full_file_path, index=False)

In [64]:
def circle_map2():
    
    # Create a base map centered around Tokyo, Japan
    m = folium.Map(location=[35.652832, 139.839478], zoom_start=13)

    # Add the narita marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
    narita.add_to(m)

    # Add the haneda marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
    haneda.add_to(m)

    # Add Starbucks locations to the map
    for location in starbucks:
        tooltip = location['name']
        icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add other markers from tok_df to the map
    for index, row in tok_df.iterrows():
        tooltip = row['name']
        icon = folium.Icon(color='purple', icon_color='white', icon='gamepad', prefix='fa')
        folium.Marker(location=[row['lat'], row['lon']], tooltip=tooltip, icon=icon).add_to(m)
    

    # Add the successful tech startups that have coordinates    
    for index, row in start.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='red', icon_color='white', icon='cloud-upload', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lon']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
          
    # Add the pet grooming places    
    for location in dog:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add the train stations   
    for location in train:
        tooltip = location['name']
        icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    # Add the karaokes so that the employees can have fun

    for location in kara:
        tooltip = location['name']
        icon = folium.Icon(color='black', icon_color='white', icon='microphone', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    for location in veg:
        tooltip = location['name']
        icon = folium.Icon(color='green', icon_color='white', icon='leaf', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
        
    for location in guardes:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='black', icon='child', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
        
    # Add circles with a ratio of the closest things
    
    circles = [
        {"center": [35.669185, 139.734548], "radius": 1500, "color": "red",},
        {"center": [35.657591, 139.699055], "radius": 1500, "color": "blue"},
        {"center": [35.627796, 139.740745], "radius": 1500, "color": "green"},
        {"center": [35.661512, 139.728418], "radius": 1500, "color": "orange"},
        {"center": [35.673578, 139.764248], "radius": 1500, "color": "purple"},
        {"center": [35.673165, 139.738309], "radius": 1500, "color": "yellow"},
        {"center": [35.693763, 139.703632], "radius": 1500, "color": "gray"}
        
    ]

    for circle_info in circles:
        circle_center = circle_info["center"]
        circle_radius = circle_info["radius"]
        circle_color = circle_info["color"]

        folium.Circle(
            location=circle_center,
            radius=circle_radius,
            color=circle_color,
            fill=True,
            fill_color=circle_color,
            fill_opacity=0.2
        ).add_to(m)

    return m

In [65]:
circle_map2()

/var/folders/_b/4s7pp99j1qq9lxsqpjphc78m0000gn/T/ipykernel_83833/1834896500.py:19: UserWarning: color argument of Icon should be one of: {'lightgreen', 'darkgreen', 'pink', 'gray', 'green', 'lightgray', 'darkblue', 'white', 'black', 'purple', 'blue', 'beige', 'darkred', 'cadetblue', 'red', 'lightred', 'lightblue', 'orange', 'darkpurple'}.
  icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')


In [66]:
def circle_map0():
    
    # Create a base map centered around Tokyo, Japan
    m = folium.Map(location=[35.652832, 139.839478], zoom_start=13)

    # Add the narita marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
    narita.add_to(m)

    # Add the haneda marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
    haneda.add_to(m)


    # Add other markers from tok_df to the map
    for index, row in tok_df.iterrows():
        tooltip = row['name']
        icon = folium.Icon(color='purple', icon_color='white', icon='gamepad', prefix='fa')
        folium.Marker(location=[row['lat'], row['lon']], tooltip=tooltip, icon=icon).add_to(m)
    

    # Add the successful tech startups that have coordinates    
    for index, row in start.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='red', icon_color='white', icon='cloud-upload', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lon']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
          
    # pet places
    
    for index, row in dog_d.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lng']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
            
     # elementary school
    
    for index, row in guardes_d.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='blue', icon_color='black', icon='child', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lng']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
            
     # karaokes
    
    for index, row in kara_d.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='black', icon_color='white', icon='microphone', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lng']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
            
    # starbucks
    
    for index, row in starbucks_d.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='red', icon_color='black', icon='coffee', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lng']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
            
            
    # metro stations
    
    for index, row in train_d.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lng']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
            
            
    # vegan places
    
    for index, row in veg_d.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='green', icon_color='white', icon='leaf', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lng']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
        
    # Add circles with a ratio of the closest things
    
    circles = [
        {"center": [35.669185, 139.734548], "radius": 1500, "color": "red",},
        {"center": [35.657591, 139.699055], "radius": 1500, "color": "blue"},
        {"center": [35.627796, 139.740745], "radius": 1500, "color": "green"},
        {"center": [35.661512, 139.728418], "radius": 1500, "color": "orange"},
        {"center": [35.673578, 139.764248], "radius": 1500, "color": "purple"},
        {"center": [35.673165, 139.738309], "radius": 1500, "color": "yellow"},
        {"center": [35.693763, 139.703632], "radius": 1500, "color": "gray"}
        
    ]

    for circle_info in circles:
        circle_center = circle_info["center"]
        circle_radius = circle_info["radius"]
        circle_color = circle_info["color"]

        folium.Circle(
            location=circle_center,
            radius=circle_radius,
            color=circle_color,
            fill=True,
            fill_color=circle_color,
            fill_opacity=0.2
        ).add_to(m)

    return m

In [67]:
circle_map0()

In [68]:
def circle_map3():
    
    # Create a base map centered around Tokyo, Japan
    m = folium.Map(location=[35.652832, 139.839478], zoom_start=13)

    # Add the narita marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
    narita.add_to(m)

    # Add the haneda marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
    haneda.add_to(m)

    # Add Starbucks locations to the map
    for location in starbucks:
        tooltip = location['name']
        icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add other markers from tok_df to the map
    for index, row in tok_df.iterrows():
        tooltip = row['name']
        icon = folium.Icon(color='purple', icon_color='white', icon='gamepad', prefix='fa')
        folium.Marker(location=[row['lat'], row['lon']], tooltip=tooltip, icon=icon).add_to(m)
    

    # Add the successful tech startups that have coordinates    
    for index, row in start.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='red', icon_color='white', icon='cloud-upload', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lon']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
          
    # Add the pet grooming places    
    for location in dog:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add the train stations   
    for location in train:
        tooltip = location['name']
        icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    # Add the karaokes so that the employees can have fun

    for location in kara:
        tooltip = location['name']
        icon = folium.Icon(color='black', icon_color='white', icon='microphone', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    for location in veg:
        tooltip = location['name']
        icon = folium.Icon(color='green', icon_color='white', icon='leaf', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
        
    for location in guardes:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='black', icon='child', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
        
    # Add circles with a ratio of the closest things
    
    circles = [
        {"center": [35.669185, 139.734548], "radius": 1500, "color": "red",},
        {"center": [35.661512, 139.728418], "radius": 1500, "color": "orange"},
        {"center": [35.673165, 139.738309], "radius": 1500, "color": "yellow"},
        
        
    ]

    for circle_info in circles:
        circle_center = circle_info["center"]
        circle_radius = circle_info["radius"]
        circle_color = circle_info["color"]

        folium.Circle(
            location=circle_center,
            radius=circle_radius,
            color=circle_color,
            fill=True,
            fill_color=circle_color,
            fill_opacity=0.2
        ).add_to(m)

    return m

In [69]:
circle_map3()

/var/folders/_b/4s7pp99j1qq9lxsqpjphc78m0000gn/T/ipykernel_83833/4223449968.py:19: UserWarning: color argument of Icon should be one of: {'lightgreen', 'darkgreen', 'pink', 'gray', 'green', 'lightgray', 'darkblue', 'white', 'black', 'purple', 'blue', 'beige', 'darkred', 'cadetblue', 'red', 'lightred', 'lightblue', 'orange', 'darkpurple'}.
  icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')


In [70]:
def circle_map4():
    
    # Create a base map centered around Tokyo, Japan
    m = folium.Map(location=[35.661512, 139.728418], zoom_start=13)

    # Add the narita marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
    narita.add_to(m)

    # Add the haneda marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
    haneda.add_to(m)

    # Add Starbucks locations to the map
    for location in starbucks:
        tooltip = location['name']
        icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add other markers from tok_df to the map
    for index, row in tok_df.iterrows():
        tooltip = row['name']
        icon = folium.Icon(color='purple', icon_color='white', icon='gamepad', prefix='fa')
        folium.Marker(location=[row['lat'], row['lon']], tooltip=tooltip, icon=icon).add_to(m)
    

    # Add the successful tech startups that have coordinates    
    for index, row in start.iterrows():
            tooltip = row['name']
            icon = folium.Icon(color='red', icon_color='white', icon='cloud-upload', prefix='fa')
            folium.Marker(
                location=[row['lat'], row['lon']],
                tooltip=tooltip,
                icon=icon
                ).add_to(m)
          
    # Add the pet grooming places    
    for location in dog:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add the train stations   
    for location in train:
        tooltip = location['name']
        icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    # Add the karaokes so that the employees can have fun

    for location in kara:
        tooltip = location['name']
        icon = folium.Icon(color='black', icon_color='white', icon='microphone', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    for location in veg:
        tooltip = location['name']
        icon = folium.Icon(color='green', icon_color='white', icon='leaf', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
        
    for location in guardes:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='black', icon='child', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
        

    return m

In [71]:
circle_map4()

/var/folders/_b/4s7pp99j1qq9lxsqpjphc78m0000gn/T/ipykernel_83833/1369571300.py:19: UserWarning: color argument of Icon should be one of: {'lightgreen', 'darkgreen', 'pink', 'gray', 'green', 'lightgray', 'darkblue', 'white', 'black', 'purple', 'blue', 'beige', 'darkred', 'cadetblue', 'red', 'lightred', 'lightblue', 'orange', 'darkpurple'}.
  icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')


In [72]:
def circle_map5():
    
    # Create a base map centered around Tokyo, Japan
    m = folium.Map(location=[35.656467,139.7318437], zoom_start=15)

    # Add the narita marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    narita = folium.Marker(location=[lati, longi], tooltip="Narita Airport", icon=icon)
    narita.add_to(m)

    # Add the haneda marker
    icon = folium.Icon(color='pink', icon_color='white', icon='plane', prefix='fa')
    haneda = folium.Marker(location=[latu, longu], tooltip="Haneda Airport", icon=icon)
    haneda.add_to(m)

    # Add Starbucks locations to the map
    for location in starbucks:
        tooltip = location['name']
        icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add other markers from tok_df to the map
    for index, row in tok_df.iterrows():
        tooltip = row['name']
        icon = folium.Icon(color='purple', icon_color='white', icon='gamepad', prefix='fa')
        folium.Marker(location=[row['lat'], row['lon']], tooltip=tooltip, icon=icon).add_to(m)
    

    # Add the successful tech startups that have coordinates    
    for index, row in start.iterrows():
        tooltip = row['name']
        icon = folium.Icon(color='red', icon_color='white', icon='cloud-upload', prefix='fa')
        folium.Marker(
        location=[row['lat'], row['lon']],
        tooltip=tooltip,
        icon=icon
        ).add_to(m)
          
    # Add the pet grooming places    
    for location in dog:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='white', icon='paw', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)

    # Add the train stations   
    for location in train:
        tooltip = location['name']
        icon = folium.Icon(color='orange', icon_color='black', icon='train', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    # Add the karaokes so that the employees can have fun

    for location in kara:
        tooltip = location['name']
        icon = folium.Icon(color='black', icon_color='white', icon='microphone', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
    
    for location in veg:
        tooltip = location['name']
        icon = folium.Icon(color='green', icon_color='white', icon='leaf', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
        
    for location in guardes:
        tooltip = location['name']
        icon = folium.Icon(color='blue', icon_color='black', icon='child', prefix='fa')
        folium.Marker([location['lat'], location['lng']], tooltip=tooltip, icon=icon).add_to(m)
        
        
    # Add circles with a ratio of the closest things
    circle_center = [35.6555691, 139.7343113] # I have chosen this center because it's a dog grooming place that it's nearby to all the things required.
    circle_radius = 900 
    circle_radius_2 = 1500

    # Create a circle with the specified center and radius
    folium.Circle(location=circle_center, radius=circle_radius, color='red', fill=True, fill_color='red', fill_opacity=0.2).add_to(m)
    folium.Circle(location=circle_center, radius=circle_radius_2, color='blue', fill=True, fill_color='red', fill_opacity=0.2).add_to(m)

    return m

In [73]:
circle_map5()

/var/folders/_b/4s7pp99j1qq9lxsqpjphc78m0000gn/T/ipykernel_83833/519718377.py:19: UserWarning: color argument of Icon should be one of: {'lightgreen', 'darkgreen', 'pink', 'gray', 'green', 'lightgray', 'darkblue', 'white', 'black', 'purple', 'blue', 'beige', 'darkred', 'cadetblue', 'red', 'lightred', 'lightblue', 'orange', 'darkpurple'}.
  icon = folium.Icon(color='brown', icon_color='black', icon='coffee', prefix='fa')
